## SDK code to create CUSTOMER_Variability_of_invoice_Weekday_based_on_invoice_Amount_28d

Feature description:
>The feature evaluates the distribution of a customer's invoice's Amount across various invoice's Weekday categories over a 28d period using entropy. Higher entropy signifies a more uniform distribution of invoice's Amount across categories, while lower entropy suggests a concentration within specific invoice's Weekday categories.

In [ ]:
import featurebyte as fb
fb.use_profile("tutorial")

### Activate catalog

 See [SDK reference for catalogs](https://docs.featurebyte.com/latest/reference/core/catalog/)

In [ ]:
catalog = fb.Catalog.activate("Grocery Dataset Tutorial")

### Set windows for aggregation

In [ ]:
windows = ['28d']

### Get view from table
 See [SDK reference for views](https://docs.featurebyte.com/latest/reference/core/view/)

In [ ]:
# Get view from GROCERYINVOICE event table.
groceryinvoice_view = catalog.get_view("GROCERYINVOICE")

### Extract Date parts
 See [SDK reference for view columns](https://docs.featurebyte.com/latest/reference/core/view_column/)

 See [list of datetime transforms](https://docs.featurebyte.com/latest/about/glossary/#datetime-transforms)

In [ ]:
# Extract day_of_week date part from Timestamp column for GROCERYINVOICE view.
groceryinvoice_view["Weekday of invoice"] = groceryinvoice_view["Timestamp"].dt.day_of_week

### Do window aggregation from GROCERYINVOICE
 See [SDK reference for features](https://docs.featurebyte.com/latest/reference/core/feature/)

 See [SDK reference to groupby a view](https://docs.featurebyte.com/latest/reference/featurebyte.api.view.GroupByMixin.groupby/)

 See [SDK reference to do aggregation over time](https://docs.featurebyte.com/latest/reference/featurebyte.api.groupby.GroupBy.aggregate_over/)

 See [SDK reference for feature group](https://docs.featurebyte.com/latest/reference/core/feature_group/)

 See [list of aggregation operations](https://docs.featurebyte.com/latest/reference/featurebyte.enum.AggFunc/)

In [ ]:
# Group GROCERYINVOICE view by customer entity (GroceryCustomerGuid) across different Weekday of
# invoices.
groceryinvoice_view_by_customer_across_weekday_of_invoice =\
groceryinvoice_view.groupby(
    ['GroceryCustomerGuid'], category="Weekday of invoice"
)

In [ ]:
# Distribution representing the cumulative Amount of invoice, categorized by their respective
# invoice's Weekday, for the customer over time.
feature_group =\
groceryinvoice_view_by_customer_across_weekday_of_invoice.aggregate_over(
    "Amount", method=fb.AggFunc.SUM,
    feature_names=[
        "CUSTOMER_invoice_Amount_across_invoice_Weekdays"
        + "_" + w for w in windows
    ],
    windows=windows
)
# Get CUSTOMER_invoice_Amount_across_invoice_Weekdays_28d object from feature group.
customer_invoice_amount_across_invoice_weekdays_28d =\
feature_group["CUSTOMER_invoice_Amount_across_invoice_Weekdays_28d"]

### Derive feature from aggregation across categories
 See [list of feature transforms](https://docs.featurebyte.com/latest/about/glossary/#feature-transforms)

In [ ]:
# Get Variability of invoice Weekday based on invoice Amount from
# CUSTOMER_invoice_Amount_across_invoice_Weekdays_28d
customer_variability_of_invoice_weekday_based_on_invoice_amount_28d =\
customer_invoice_amount_across_invoice_weekdays_28d.cd.entropy()
# Give a name to new feature
customer_variability_of_invoice_weekday_based_on_invoice_amount_28d.name = \
"CUSTOMER_Variability_of_invoice_Weekday_based_on_invoice_Amount_28d"

### Preview feature
 Read on [the feature primary entity concept](https://docs.featurebyte.com/latest/about/glossary/#feature-primary-entity)

 Read on [the serving entity concept](https://docs.featurebyte.com/latest/about/glossary/#serving-entity)

 See [SDK reference for observation table](https://docs.featurebyte.com/latest/reference/core/observation_table/)

 See [SDK reference to preview feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.preview/)

In [ ]:
#Check the primary entity of the feature'
customer_variability_of_invoice_weekday_based_on_invoice_amount_28d.primary_entity

In [ ]:
#Get observation table: 'Preview Table with 10 Customers'
preview_table = catalog.get_observation_table(
	"Preview Table with 10 Customers"
).to_pandas()

In [ ]:
#Preview CUSTOMER_Variability_of_invoice_Weekday_based_on_invoice_Amount_28d
customer_variability_of_invoice_weekday_based_on_invoice_amount_28d.preview(
	preview_table
)

### Save feature
 See [SDK reference to save feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.save/)

In [ ]:
# Save feature
customer_variability_of_invoice_weekday_based_on_invoice_amount_28d.save()

### Add description and see feature definition file
 See [SDK reference for the definition file of a feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.definition/)

In [ ]:
# Add description
customer_variability_of_invoice_weekday_based_on_invoice_amount_28d.update_description(
	"The feature evaluates the distribution of a customer's invoice's "
	"Amount across various invoice's Weekday categories over a 28d period "
	"using entropy. Higher entropy signifies a more uniform distribution of"
	" invoice's Amount across categories, while lower entropy suggests a "
	"concentration within specific invoice's Weekday categories."
)
# See feature definition file
customer_variability_of_invoice_weekday_based_on_invoice_amount_28d.definition